In [9]:
import os
from collections import Counter, defaultdict
from tqdm import tqdm
import matplotlib.pyplot as plt
import matplotlib.dates as mdates
import datetime as dt
import json
import csv
import pandas as pd
import seaborn as sns

In [2]:
sns.set(style="whitegrid")
sns.set(rc={'figure.figsize':(11.7,8.27)})

In [19]:
ROOT = '/mnt/data0/lucy/manosphere/'
SUBS = ROOT + 'data/submissions/'
SUB_META = ROOT + 'data/subreddits.txt'
LOGS = ROOT + 'logs/'
PEOPLE_FILE = ROOT + 'data/people.csv'
SUB_META = ROOT + 'data/subreddits.txt'

# Glossary matches

In [82]:
def get_manual_people(): 
    """
    get list of words, add plural forms
    copied from find_people.py
    """
    words = set()
    sing2plural = {}
    with open(PEOPLE_FILE, 'r') as csvfile:
        reader = csv.DictReader(csvfile)
        for row in reader: 
            word_sing = row['word (singular)'].strip()
            plural = row['word (plural)'].strip()
            if word_sing != '':
                if word_sing.lower() in words: print('REPEAT', word_sing)
                words.add(word_sing.lower())
                sing2plural[word_sing] = plural
            if plural != '': 
                if plural.lower() in words: print('REPEAT', plural)
                assert word_sing != ''
                words.add(plural.lower())
    return words, sing2plural

In [20]:
def get_subreddit_categories(): 
    categories = defaultdict(str)
    categories_rev = defaultdict(list)
    with open(SUB_META, 'r') as infile: 
        reader = csv.DictReader(infile)
        for row in reader: 
            name = row['Subreddit'].strip().lower()
            if name.startswith('/r/'): name = name[3:]
            if name.startswith('r/'): name = name[2:]
            if name.endswith('/'): name = name[:-1]
            categories[name] = row['Category after majority agreement']
            categories_rev[row['Category after majority agreement']].append(name)
    return categories, categories_rev

In [21]:
categories, categories_rev = get_subreddit_categories()

In [4]:
with open(LOGS + 'glossword_one_month.temp', 'r') as infile: 
    d = json.load(infile)

In [29]:
people, sing2plural = get_manual_people()
people_counts_sr = defaultdict(Counter)
people_counts_cat = defaultdict(Counter)
for sr in d: 
    cat = categories[sr[8:]]
    for term in d[sr]: 
        if term in sing2plural:
            plural = sing2plural[term]
            if plural not in d[sr]: 
                plural_count = 0
            else: 
                plural_count = d[sr][plural]
            total_count = d[sr][term] + plural_count
            people_counts_sr[sr][term] = total_count
            people_counts_cat[cat][term] += total_count

In [31]:
for sr in people_counts_sr: 
    print(sr)
    for tup in people_counts_sr[sr].most_common(10): 
        if tup[1] > 0: 
            print(tup,)
    print()

2016-03_depression
('gf', 184)
('natural', 163)
('bro', 96)
('void', 95)
('bf', 90)
('tool', 82)
('primary', 61)
('obstacle', 46)
('robot', 45)
('target', 34)

2016-03_foreveralone
('normie', 280)
('gf', 164)
('bro', 90)
('nice guy', 89)
('natural', 64)
('bf', 60)
('alpha', 60)
('jaw', 48)
('beta', 39)
('pua', 34)

2016-03_mensrights
('mra', 1004)
('sjw', 452)
('wing', 379)
('primary', 197)
('mgtow', 182)
('natural', 144)
('target', 139)
('tool', 138)
('misogynist', 135)
('bro', 102)

2016-03_theredpill
('beta', 2651)
('alpha', 2590)
('natural', 659)
('bro', 446)
('mgtow', 388)
('pua', 382)
('tool', 315)
('sjw', 303)
('gf', 296)
('unicorn', 245)

2016-03_thebluepill
('alpha', 695)
('beta', 284)
('mgtow', 176)
('cuck', 136)
('mra', 133)
('bro', 102)
('natural', 99)
('misogynist', 82)
('nice guy', 75)
('alpha male', 75)

2016-03_asktrp
('beta', 1085)
('alpha', 943)
('gf', 310)
('bro', 309)
('natural', 264)
('orbiter', 170)
('nice guy', 139)
('pua', 116)
('bf', 111)
('tool', 100)

2016-03

In [32]:
for cat in people_counts_cat:
    print(cat)
    for tup in people_counts_cat[cat].most_common(10): 
        if tup[1] > 0: 
            print(tup,)
    print()

Health
('natural', 261)
('gf', 242)
('bf', 142)
('bro', 141)
('void', 132)
('tool', 124)
('primary', 83)
('obstacle', 62)
('robot', 56)
('lover', 50)

Incels
('normie', 378)
('gf', 186)
('incel', 135)
('nice guy', 129)
('alpha', 117)
('bro', 104)
('beta', 79)
('natural', 74)
('bf', 66)
('pua', 63)

MRA
('mra', 1035)
('sjw', 463)
('wing', 382)
('primary', 198)
('mgtow', 182)
('tool', 146)
('natural', 145)
('target', 139)
('misogynist', 136)
('bro', 107)

TRP
('beta', 4159)
('alpha', 4002)
('natural', 1032)
('bro', 788)
('gf', 641)
('pua', 530)
('tool', 507)
('mgtow', 466)
('nice guy', 419)
('sjw', 384)

Criticism
('alpha', 731)
('beta', 318)
('mgtow', 218)
('mra', 187)
('cuck', 138)
('bro', 106)
('natural', 106)
('nice guy', 93)
('misogynist', 88)
('sjw', 81)

MGTOW
('mgtow', 2126)
('beta', 251)
('alpha', 179)
('sjw', 152)
('pua', 151)
('bro', 120)
('unicorn', 103)
('gf', 93)
('white knight', 93)
('natural', 92)

PUA
('nice guy', 214)
('pua', 203)
('bro', 178)
('natural', 165)
('alpha',

# BookNLP NER tagged people

In [88]:
POSTS = ROOT + 'data/submissions/'
COMMENTS = ROOT + 'data/comments/'

In [89]:
all_entities = Counter()
with open(LOGS + 'tagged_people/2016-03', 'r') as infile: 
    for line in infile: 
        entities = line.split('\t')
        for entity in entities: 
            if entity.strip() == '': continue
            person = entity.lower().split()[2:]
            if person[0] == 'a' or person[0] == 'an' or person[0] == 'the': 
                person = person[1:]
            person = ' '.join(person)
            all_entities[person] += 1

In [90]:
all_entities.most_common()

[('women', 33676),
 ('people', 24529),
 ('men', 20482),
 ('someone', 10379),
 ('man', 9416),
 ('woman', 8572),
 ('everyone', 6422),
 ('girl', 5592),
 ('girls', 5435),
 ('anyone', 5084),
 ('friends', 4762),
 ('no one', 3983),
 ('child', 3207),
 ('others', 3191),
 ('guy', 3153),
 ('other people', 2850),
 ('guys', 2699),
 ('kids', 2471),
 ('person', 2440),
 ('feminists', 2382),
 ('my parents', 2319),
 ('family', 2254),
 ('children', 2223),
 ('nobody', 2186),
 ('my friends', 1977),
 ('friend', 1817),
 ('my family', 1769),
 ('someone else', 1748),
 ('some people', 1702),
 ('most people', 1693),
 ('dude', 1637),
 ('my mom', 1579),
 ('', 1502),
 ('this guy', 1449),
 ('my dad', 1397),
 ('kid', 1382),
 ('this girl', 1349),
 ('my wife', 1330),
 ('my friend', 1199),
 ('boys', 1167),
 ('doctor', 1150),
 ('father', 1140),
 ('my mother', 1049),
 ('therapist', 1039),
 ('mother', 1011),
 ('wife', 989),
 ('male', 947),
 ('everyone else', 941),
 ('anyone else', 923),
 ('female', 857),
 ('your wife', 843

In [91]:
people, sing2plural = get_manual_people()

In [92]:
uncounted = set()
for person in people: 
    if person in all_entities: 
        print(person, all_entities[person])
    else: 
        uncounted.add(person)

social butterfly 12
misogynists 53
western women 71
mras 168
lone wolves 2
stay at home mothers 2
lover 35
nymphos 1
roastie 1
afc 7
mc 6
foreign woman 4
hot babes 2
chad 106
bf 14
hb 3
real man 131
stalkers 6
incel 8
primary 4
lovers 25
feminazi 25
feminazis 44
naturals 8
robots 27
dancing monkey 3
amog 12
cheaters 30
femtards 1
nice guy 319
western woman 14
lone wolf 30
landwhales 1
entourage 5
bunny 4
orbiters 22
hater 12
gamers 33
red pill women 3
role model 19
traditionalists 11
mgtows 32
djs 5
prude 9
poster boy 1
providers 38
stalker 28
beta males 52
pug 1
provider 109
beta 309
conformists 3
wizard 15
role models 10
nympho 4
incels 3
red pill woman 8
dj 24
neets 2
observers 6
landwhale 6
pick up masters 1
femtard 2
pickup artist 10
cucks 21
unicorn 32
subhuman 1
prudes 4
aspies 4
mra 182
cheater 54
truecel 2
manlet 5
otaku 1
hugger 1
white knights 98
alphas 234
foreign women 15
normies 43
false prophet 1
pick up master 1
wingwomen 3
alpha 467
gf 26
beta male 29
seducer 4
real me

In [93]:
uncounted

{'ab',
 "ab's",
 'absolute beginner',
 'add girl',
 'add girls',
 'afog',
 'afogs',
 'amogs',
 'androphile',
 'androphiles',
 'apua',
 'apuas',
 'arbitrary target',
 'arbitrary target s',
 'bafc',
 'bafcs',
 'becky',
 'beckys',
 'betabuxx',
 'betabuxxes',
 'betafag',
 'betafags',
 'black bunny',
 'black bunnys',
 'blackcel',
 'blackcels',
 'blue bunny',
 'blue bunnys',
 'bottom feeders',
 'breakup artist',
 'breakup artists',
 'bunnys',
 'casanovas',
 'celebrity pua',
 'celebrity puas',
 'chaddam',
 'chaddams',
 'chadlite',
 'chadlites',
 'chadpreet',
 'chadpreets',
 'chadrone',
 'chadrones',
 'chang',
 'changs',
 'chit chat master',
 'chit chat masters',
 'christian pua',
 'christian puas',
 'club girl',
 'club girls',
 'cock tease',
 'cock teases',
 'comfort whore',
 'comfort whores',
 'cougar',
 'cum dumpsters',
 'cum rag',
 'cum rags',
 'cumdumpster',
 'cumdumpsters',
 'currycel',
 'currycels',
 'cybercel',
 'cybercels',
 'dance floor monkey',
 'dance floor monkeys',
 'dancing monk

In [94]:
# what kinds of uncounted people appear in subreddits? 
for person in uncounted: 
    for sr in people_counts_sr: 
        if person in people_counts_sr[sr]: 
            if people_counts_sr[sr][person] != 0: 
                print(sr, person, people_counts_sr[sr][person])

2016-03_foreveralone cougar 1
2016-03_mensrights cougar 5
2016-03_theredpill cougar 14
2016-03_thebluepill cougar 2
2016-03_asktrp cougar 4
2016-03_mgtow cougar 1
2016-03_seduction cougar 3
2016-03_askseddit cougar 4
2016-03_foreverunwanted cougar 2
2016-03_foreveralone try-hard 1
2016-03_theredpill try-hard 9
2016-03_thebluepill try-hard 2
2016-03_asktrp try-hard 8
2016-03_seduction try-hard 3
2016-03_askseddit try-hard 2
2016-03_marriedredpill try-hard 2
2016-03_mensrights keyboard jockey 1
2016-03_theredpill keyboard jockey 7
2016-03_asktrp keyboard jockey 1
2016-03_mensrights transtrender 2
2016-03_depression chang 1
2016-03_mensrights chang 1
2016-03_theredpill chang 1
2016-03_asktrp betafag 1
2016-03_mensrights ladies' man 1
2016-03_seduction ladies' man 1
2016-03_suicidewatch ladies' man 1
2016-03_mensrights kj 4
2016-03_theredpill kj 1
2016-03_theredpill volcel 1
2016-03_truecels volcel 1
2016-03_theredpill club girl 2
2016-03_depression void 95
2016-03_foreveralone void 9
2016

In [105]:
all_entities['just another wannabe']

0

In [95]:
line2entities = defaultdict(list)
with open(LOGS + 'tagged_people/2016-03', 'r') as infile: 
    for i, line in enumerate(infile): 
        entities = line.split('\t')
        for entity in entities: 
            if entity.strip() == '': continue
            person = entity.lower().split()[2:]
            if person[0] == 'a' or person[0] == 'an' or person[0] == 'the': 
                person = person[1:]
            person = ' '.join(person)
            line2entities[i].append(person)

In [96]:
# Where are some words possibly being missed? 
i = 0
month = '2016-03'
with open(COMMENTS + 'RC_' + month + '/part-00000', 'r') as infile: 
    for line in infile: 
        d = json.loads(line)
        text = d['body']
        if 'omegas' in text: 
            if 'omegas' not in line2entities[i]: 
                print("------------------------------")
                print(text)
                print("------------------------------")
        i += 1
if os.path.exists(POSTS + 'RS_' + month + '/part-00000'): 
    post_path = POSTS + 'RS_' + month + '/part-00000'
else: 
    post_path = POSTS + 'RS_v2_' + month + '/part-00000'
with open(post_path, 'r') as infile: 
    for line in infile: 
        d = json.loads(line)
        text = d['selftext']
        if 'omegas' in text: 
            if 'omegas' not in line2entities[i]: 
                print("------------------------------")
                print(text)
                print("------------------------------")
        i += 1

------------------------------
&gt;The omegas are on a whole other level. Not only are they short, fat, and unattractive, these men are really invisible to you. Why? Because they do not even bother with women. They go play video games all day. They cannot for the life of them attract a woman. They go in front of a woman and stutter and twiddle their thumbs and do their best to muster “D-d-do y-you want, uh, um, to um l-like go on a d-d-d-date with me” and the poor woman cannot help but feel her vagina dry up like the Sahara Desert.

&gt;These men are about 80% of the male population to you (give or take 5%). 

Really? 80% of the male population is like that?

Dude, just because you're like that and your friends are like that doesn't mean the vast majority of the population is like that. 
------------------------------
------------------------------
So in 5 months you gained 17 pounds?  Ya.  Get your terminology straight.  That is straight up bulking.  Or are you one of them posers who 

------------------------------
Within the general ideas of Hypergamy, it's believed that woman only really go for the top 20% of men.  This would align with the 80/20 rule.  Whether this top 20% applies to looks or money or game, I don't know, but stay with me here.  

Would this mean that a guy just below the 80% threshold would get shit tested the most?  Woman are unlikely to test a guy who is DEFINITELY in the top tier, and they would likely ignore (not even bother to test) a guy who is DEFINITELY far away from that threshold.

But what about a guy who is 70-something % ??  Is he going to get the worst of it because it's not so obvious to her?  

Speaking for myself, I think I may have been there for a while and when my lifting got really consistant, I almost definitely surpassed the 80% mark.  Since then I get almost non-stop positive attention and no shit testing.  Meanwhile, my younger brother and some friends (who are betas bordering on omegas) never get any positive attention, 

In [98]:
# What are possible new words not in glossaries? 
# note that right now, manual people does not include generic words
for person in all_entities.most_common(): 
    if person[0] not in people: 
        print(person)

('women', 33676)
('people', 24529)
('men', 20482)
('someone', 10379)
('man', 9416)
('woman', 8572)
('everyone', 6422)
('girl', 5592)
('girls', 5435)
('anyone', 5084)
('friends', 4762)
('no one', 3983)
('child', 3207)
('others', 3191)
('guy', 3153)
('other people', 2850)
('guys', 2699)
('kids', 2471)
('person', 2440)
('feminists', 2382)
('my parents', 2319)
('family', 2254)
('children', 2223)
('nobody', 2186)
('my friends', 1977)
('friend', 1817)
('my family', 1769)
('someone else', 1748)
('some people', 1702)
('most people', 1693)
('dude', 1637)
('my mom', 1579)
('', 1502)
('this guy', 1449)
('my dad', 1397)
('kid', 1382)
('this girl', 1349)
('my wife', 1330)
('my friend', 1199)
('boys', 1167)
('doctor', 1150)
('father', 1140)
('my mother', 1049)
('therapist', 1039)
('mother', 1011)
('wife', 989)
('male', 947)
('everyone else', 941)
('anyone else', 923)
('female', 857)
('your wife', 843)
('girlfriend', 813)
('somebody', 812)
('many people', 797)
('parents', 778)
('victim', 775)
('these

('female players', 9)
('pool boy', 9)
('cultural libertarians', 9)
('entps', 9)
('crown', 9)
('ghomeshi', 9)
('shared national narrative', 9)
('composer', 8)
('chemical engineer', 8)
('best version of you', 8)
('good girlfriend', 8)
('founders', 8)
('any group', 8)
('women on tinder', 8)
('abusive parents', 8)
('terrible human being', 8)
('these betas', 8)
('2 children', 8)
('woman like', 8)
('ec', 8)
('investment banker', 8)
('girl like this', 8)
('dumb bitch', 8)
('super', 8)
("' nice guy", 8)
('companions', 8)
('spoiled brat', 8)
('every individual', 8)
('2 men', 8)
('lonely person', 8)
('any human', 8)
('one good friend', 8)
('pilots', 8)
('all females', 8)
('6 year old', 8)
('female workers', 8)
('bodies', 8)
('abusive alcoholic', 8)
('someone else who', 8)
('modern western woman', 8)
('health officials', 8)
('any close friends', 8)
('female mras', 8)
('indian guys', 8)
('hot one', 8)
('recipient', 8)
('damn son', 8)
('each parent', 8)
('younger sister', 8)
('my abuser', 8)
('perf

('your loved one', 4)
('30 + year old women', 4)
('short dudes', 4)
('your reflection', 4)
('most people in this sub', 4)
('older generation', 4)
('same teacher', 4)
('joke', 4)
('woman in', 4)
('some white knights', 4)
('girl i was seeing', 4)
('female coworker', 4)
('slacker', 4)
('enigma', 4)
('lovely', 4)
('high value woman', 4)
('two different girls', 4)
('feminine imperative', 4)
('her bro', 4)
('awesome friends', 4)
('anti - men', 4)
('crazy girl', 4)
('my step mother', 4)
('chill dude', 4)
('people who commit suicide', 4)
('girls here', 4)
('wanker', 4)
('family guy', 4)
('rpw community', 4)
('that whore', 4)
('actual victims', 4)
('boogeyman', 4)
('consultants', 4)
('every attractive woman', 4)
('bank teller', 4)
('male coworkers', 4)
('my superiors', 4)
('always', 4)
('this jerk', 4)
('all parties involved', 4)
('most people with depression', 4)
('civil engineer', 4)
('vigilante', 4)
('cleaner', 4)
('their own citizens', 4)
('no siblings', 4)
('hotline', 4)
('ones who say', 4

('no one else around', 3)
('any gender', 3)
('only one man', 3)
('media outlets', 3)
('her two kids', 3)
('grand child', 3)
('no dipshit', 3)
('11 men', 3)
('lot of different types of people', 3)
('https://np.reddit.com/r/redpillwome', 3)
('users of this sub', 3)
('mannequins', 3)
('actual judge', 3)
('full grown men', 3)
('markedly polarized population', 3)
('disgusting liars', 3)
("child 's custodial parent", 3)
('straight person', 3)
('woman of', 3)
('someone they love', 3)
('far more people', 3)
('my english teacher', 3)
('perfect 10 woman', 3)
('evolutionary biologist', 3)
('my old therapist', 3)
('female transsexuals', 3)
('active participant', 3)
('this entitled son of a bitch', 3)
('bad mothers', 3)
('any kid', 3)
('female relative', 3)
('all the participants', 3)
('any doctors', 3)
('confident', 3)
('everyone on this subreddit', 3)
('some of her friends', 3)
('your crew', 3)
('entire group of people', 3)
('income', 3)
('bad looking guy', 3)
('dumb man', 3)
('busy people', 3)
(

('investment bankers', 2)
('gi bill', 2)
('all types of girls', 2)
("my cousin 's husband", 2)
('big boss', 2)
('disgusting person', 2)
('same doctor', 2)
('most people with social anxiety', 2)
("billionaire 's wife", 2)
('general practice doctor', 2)
('those closest to you', 2)
('company i worked for', 2)
('man you love', 2)
('nazi scientists', 2)
('anyone from mass', 2)
('" white male "', 2)
('classmates of mine', 2)
("lead singer of guns n ' roses", 2)
('ideal feminist man', 2)
('no female mozart', 2)
('lone maniac', 2)
('holier than thou liberals', 2)
('quote', 2)
('his or', 2)
('middle schoolers', 2)
("many trp'ers", 2)
('alpha male figures illustrated', 2)
('no roommates', 2)
('full grown man', 2)
('critic who counts', 2)
('doer of deeds', 2)
('man who is actually in the arena', 2)
('this crazy bitch', 2)
('her previous boyfriends', 2)
('lonely kid', 2)
('18 year old woman', 2)
('professional writer', 2)
('millennial girls', 2)
('some guy who', 2)
('unique human being', 2)
('pale

...

("couple of other girls inside of my social circle that i 've been building for these past couple of months", 1)
('poor loner', 1)
('hg9(hot gypsy', 1)
('our king', 1)
('female(she', 1)
('our captain', 1)
('extremely sexy light skinned black girl', 1)
('aforementioned friend', 1)
('guy with no legs', 1)
('lot of freelancers', 1)
('girl that looks almost identitcal to her', 1)
('hangs out with couples', 1)
('girls who like me in the first place', 1)
('disinterested girls', 1)
("those who are n't attracted already", 1)
('amateur indirect gamer like me', 1)
('disinterested man', 1)
('christian non drinker / smoker', 1)
('pretty chill and great guy', 1)
('" happy , go - lucky carefree guy', 1)
('such a supporting boyfriend', 1)
("my friend who i 've known since middle school", 1)
('weather man', 1)
('dadjokes', 1)
('most important girls', 1)
("poor puppy that 's begging to be taken care of", 1)
("girl that 's going to bring me down", 1)
('certified', 1)
('x guy', 1)
('pook', 1)
('couple of

("someone in montreal who 's seeking help", 1)
('one of their friends', 1)
('outcast drunk', 1)
('social bottom feeder', 1)
("sa people i 've tried chatting with through the internet", 1)
('old friends i actually loved', 1)
('friends that could get me weed', 1)
('kind of man who has a penis that women want in their vaginas', 1)
('those who contribute to it', 1)
('hardcore red guys', 1)
('your own personal drill sergeants', 1)
('beta - fucking - mess', 1)
('real md who happens to be irate', 1)
('guys that are starting to “ get it ”', 1)
('these magnificent bastards', 1)
('all the guys i have dated', 1)
('my psychotic mother', 1)
('somewhat upbeat and happy kind of guy', 1)
('some old friend', 1)
('" short relationships " person', 1)
('people with more social', 1)
('better characters', 1)
('some innocent people', 1)
('my character(no father figure', 1)
('church elders', 1)
('very accomplished and praiseworthy feminists', 1)
('" male woman', 1)
('feminine boy', 1)
('horse in drag', 1)
('c

('boring , awkward fuck up like', 1)
('“ mandated reporters', 1)
('“ suicide risk ”', 1)
('“ child abuser', 1)
('people who understand the pain of loneliness', 1)
('about 40 - 50 other kids', 1)
('half guys', 1)
('half girls', 1)
('girl on my floor', 1)
('really bad people who do', 1)
('ton of people who fake their confidence', 1)
('narcissist and dysfunctional member of society', 1)
('their kids as " smart "', 1)
('parents who praise their kids as " smart "', 1)
('some 20 year old', 1)
('superior in the corporate hierarchy', 1)
('perfect human beings', 1)
('narcissist personality disorder woman', 1)
("woman who 's so shy", 1)
('maher', 1)
('fake winner society', 1)
('idiot he truly is', 1)
('some black kid', 1)
('fatter models', 1)
('skinny models', 1)
('guy who \'s not from the 1950s who might say " i \'m not good with politics and other smart school topics', 1)
('my a couple friends of mine', 1)
('excuse', 1)
('their current employer', 1)
('truck driver with decent income', 1)
('# 3

('dangerous zealots who always needed someone less ideologically pure to denounce to ensure their position', 1)
('relatively few of these people', 1)
('unofficial revolutionary party who are there both to police the organization to ensure employees', 1)
('politically supportive students', 1)
('companies in the middle east', 1)
('members of the royal family', 1)
('children of bureaucrats and politicians', 1)
('black , green haired dyke heading up the diversity committee', 1)
('political activists', 1)
('no company with a black , green haired dyke heading up the diversity committee', 1)
('sjw police', 1)
('public companies whose ceo', 1)
('cocksuckers', 1)
('two people in love who made the decision to reproduce', 1)
('offspring of two people in love who made the decision to reproduce', 1)
('alpha douche', 1)
('offspring of an alpha douche who pumped and dumped a woman', 1)
('few public figures', 1)
('one of the few public figures whose perspectives on a lot of issues gel with rp thinking

('every man who prays or prophesies with his head covered', 1)
('every woman who prays or prophesies with her head uncovered dishonors her head', 1)
('man who puts all the burden on women', 1)
('corrupted women', 1)
('those who need', 1)
('my friends in real life', 1)
('everyone else i', 1)
('imperfect', 1)
('fu / fa community', 1)
('ones that i love', 1)
('women who are socially awkward and shut ins', 1)
('socially awkward shut in', 1)
('insert band', 1)
('best band ever', 1)
('girls who are kind of awkward in a cute , endearing way but are still generally clued up and switched on', 1)
('guys who can be shy / a little awkward', 1)
('complete fraud', 1)
('that guy with the " manboobz', 1)
('total lunatics', 1)
('lot of these kids', 1)
('no one willing', 1)
('true leaders', 1)
('this " alpha " and " true leader "', 1)
('http://www.businessinsider.com/which-sexual-fantasies-are-normal-2014-10', 1)
('53 % of men', 1)
("lot of the guys you 're arguing with , or possibly even taking advice 

In [101]:
print(all_entities['sigma'])
print('sigma' in people)

46
False
